In [1]:
import pandas as pd
import folium as folium

/Users/zerrickstaples/.pyenv/versions/3.7.0/lib/python3.7/site-packages/pandas/compat/__init__.py:117: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
  warnings.warn(msg)


In [2]:
file_path = './ColumbusParkingInfractionsData.csv'
parking_data = pd.read_csv(file_path, usecols = ['meter', 'location', 'long', 'lat', 'fine', 'badge'])
parking_df = parking_data.copy()

In [3]:
parking_df['count'] = parking_df['meter'].map(parking_df['meter'].value_counts())
parking_df.head()

badge    fine        lat         location       long  meter  count
0     12  $25.00  39.963330       YOUNG ST N -82.995520    NP9      1
1     17  $25.00  39.977910        WARREN ST -83.003340   K193      1
2     19  $25.00  40.000774       16TH AVE E -83.007744  UE377      1
3   1399  $50.00  39.973080  IFO 533 PARK ST -83.004654  NI663      1
4     16  $25.00  39.955296       PEARL ST S -82.998340  SL556      2

In [4]:
columbus_center = (39.962232, -83.000669)
columbus_map = folium.Map(
    location = columbus_center,
    zoom_start = 12,
    tiles = 'OpenStreetMap'
)

for i in range(0, len(parking_df)):
    folium.CircleMarker(
        location = [parking_df.iloc[i]['lat'], parking_df.iloc[i]['long']],
        popup = f"{parking_df.iloc[i]['meter']} {int(parking_df.iloc[i]['count'])}",
        radius = int(parking_df.iloc[i]['count'])*5,
        color = 'crimson',
        fill = True
    ).add_to(columbus_map)

# zipped_locations = zip(inventory_and_parking_data.meter, inventory_and_parking_data['lat'], inventory_and_parking_data['long'], inventory_and_parking_data['zonename'])
# for meter, lat, long, zonename in zipped_locations:
#     folium.CircleMarker(
#         location=(lat, long),
#         popup = zonename,
#         radius=1,
#         fill=True
#     ).add_to(columbus_map)

In [5]:
file_path2 = './ParkingMetersInventory2020.csv'

meter_data = pd.read_csv(file_path2, usecols = ['areaname', 'lat', 'long', 'meter number', 'subareaname', 'zonename'])
meter_data = meter_data.rename(columns = {"meter number": "meter"})
meter_df = meter_data.copy()
meter_df.head()

areaname        lat       long  meter subareaname        zonename
0  Discovery District  39.966760 -82.986160  ER622   LONG ST E     E3 Downtown
1             HIGH ST  39.985632 -83.005084   K838       31044  E2 Short North
2  Discovery District  39.966320 -82.990050  ER504   LONG ST E     E3 Downtown
3  Discovery District  39.966750 -82.986240  ER620   LONG ST E     E3 Downtown
4          POPLAR AVE  39.974447 -83.003613   K155       31064  E2 Short North

In [6]:
for i in range(0, len(meter_df)):
    folium.CircleMarker(
        location = [meter_df.iloc[i]['lat'], meter_df.iloc[i]['long']],
        popup = [meter_df.iloc[i]['meter'], meter_df.iloc[i]['areaname']],
        radius = 2.5,
        fill = True
    ).add_to(columbus_map)

In [7]:
set(meter_df['zonename'])

{'E1 Campus',
 'E2 Short North',
 'E3 Downtown',
 'E4 Franklinton',
 'E5 Brewery District',
 'E7 Grandview',
 'Test Meters',
 'Unassigned'}

In [8]:
parking_df.head()

badge    fine        lat         location       long  meter  count
0     12  $25.00  39.963330       YOUNG ST N -82.995520    NP9      1
1     17  $25.00  39.977910        WARREN ST -83.003340   K193      1
2     19  $25.00  40.000774       16TH AVE E -83.007744  UE377      1
3   1399  $50.00  39.973080  IFO 533 PARK ST -83.004654  NI663      1
4     16  $25.00  39.955296       PEARL ST S -82.998340  SL556      2

In [9]:
set(meter_df['areaname'])

{'BREWERY DISTRICT',
 'BUTTLES AVE',
 'Campus',
 'Convention Center',
 'Discovery District',
 'Downtown Business District',
 'EIGHTH AVE',
 'EUCLID AVE',
 'FIRST AVE',
 'FOURTH AVE',
 'FRANKLINTON',
 'GOODALE ST',
 'GRANDVIEW AVE',
 'GREENWOOD LOT',
 'Grant-Town',
 'HIGH ST',
 'HUBBARD AVE E',
 'LINCOLN ST',
 'NINTH AVE',
 'PARK ST',
 'PARKING LOT',
 'PEARL ST',
 'PEARL ST LOT',
 'POPLAR AVE',
 'PRICE AVE',
 'Permanently Removed',
 'RUSSELL ST E',
 'SECOND AVE',
 'STARR AVE',
 'THIRD AVE',
 'WARREN ST'}

In [10]:
parking_df = parking_df.merge(meter_data, on = 'meter')

In [11]:
fine_count_df = parking_df.groupby('zonename')["count"].sum().to_frame().reset_index()

In [12]:
fine_count_df.zonename = fine_count_df.zonename.apply(lambda x: x[3:])

In [13]:
fine_count_df

zonename  count
0            Campus     57
1       Short North    102
2          Downtown    262
3       Franklinton      1
4  Brewery District     41

In [14]:
mygeodata = r'mygeodata_merged.json'
choropleth = folium.Choropleth(
    geo_data = mygeodata,
    key_on = "feature.properties.Name",
    fill_color = "YlGn",
    data = fine_count_df,
    fill_opacity = 0.9,
    line_opacity = 0.2,
    columns = ['zonename', 'count']
).add_to(columbus_map)

choropleth.geojson.add_child(folium.features.GeoJsonTooltip(['Name']))

columbus_map